In [1]:
from tqdm import tqdm
from utils.ocr import OCRTool
from utils.pdf_splitter import split_pdf, process_pdf
import base64
from app.config import settings
from utils.emailclient import EmailAttachmentExtractor
from datetime import datetime, timedelta
from utils.sheet import SheetsClient
import pandas as pd
import logging
logger = logging.getLogger(__name__)

In [2]:
email_client = EmailAttachmentExtractor(
        email_address=settings.EMAIL_ADDRESS,
        password=settings.EMAIL_PASSWORD,
        imap_server=settings.IMAP_SERVER
        )

In [6]:
if email_client.connect():
    print("Connected to email server")
    today = datetime.now().strftime("%d-%b-%Y")
    yesterday = (datetime.now() - timedelta(days=1)).strftime("%d-%b-%Y")
    pdfs = email_client.extract_pdf_attachments(num_emails=200,
                                            subject_contains=settings.WORD_IN_SUBJECT)
                                            # date_from=yesterday,
                                            # date_to=today)

Login failed: command LOGIN illegal in state LOGOUT, only allowed in states NONAUTH


In [5]:
results = []
try:
    for pdf in pdfs:
        result = process_pdf(pdf['binary_data'], OCRTool(), pdf['filename'])
        results.append(result)
except Exception as e:
    logger.error(f"Error processing pdf: {e}")
    email_client.disconnect()

Error processing pdf: 'filename'


AttributeError: 'EmailAttachmentExtractor' object has no attribute 'disconnect'

In [23]:
sheets_client = SheetsClient(credentials_file_path=settings.CREDENTIALS_FILE_PATH)


[{'image': '...',
  'pdf': b'%PDF-1.7\n%\xc2\xb5\xc2\xb6\n\n1 0 obj\n<</Type/Catalog/Pages 2 0 R>>\nendobj\n\n2 0 obj\n<</Type/Pages/Count 1/Kids[7 0 R]>>\nendobj\n\n3 0 obj\n<</Length 125>>\nstream\nq \n1 0 0 1 2.88 2.16 cm \n829.44 0 0 606.72 0 0 cm \n/x2 Do \nQ \nq \n1 0 0 1 2.88 -1.68 cm \n806.40 0 0 610.56 0 0 cm \n/x4 Do \nQ \n\nendstream\nendobj\n\n4 0 obj\n<</Type/XObject/Subtype/Image/Width 1728/Height 1264/ColorSpace/DeviceRGB/BitsPerComponent 8/Length 15948/Filter[/FlateDecode/DCTDecode]>>\nstream\nx\x9c\xed}\x07\\Sg\xdb\xf79\ta\x89"\x18\x15T\x04D0\xa1\xa2"8p\x11\xa4 \x04\xd4\x00\x8e\x1a\xad\x03\x15\x03\xad\xab\xae\x16\x8b\x04\xad\xda\xe2BI\x15i\x95\x88\x04P\xab\xd6\x16[G\x1d\xb5\xa2\x1d\x0f\x1a\x10\xd4ZG\xeb\x04T\xac-\x96*"\xdf\xb9\xcf\xbc\xcfHH|\xfa\xb6}\xbf\xef\xeb\xf3\xfcn\xcc:\xe3:\xd7\xf8_\xf3n\xbe\xdc\xfc3\xd2V\x19\x19\x1d\x89\xa0(\x8al\xc6\xfe\x874\xbf@\xdc\x152\x1f\xb9\xd7\x88\x99sf\xbe5m\xe1\xcc\x19^\x89\xefx\x8dQ\xbe\xf2\n\xd2\xfc\x13\x12\x8e8\xda\xdb\xd9\xda;8\xd

100%|██████████| 2/2 [02:22<00:00, 71.05s/it]


In [25]:
df = pd.DataFrame(result)

In [2]:
PDF_PATH = "test_documents/chai6.11.pdf"
with open(PDF_PATH, "rb") as f:
    pdf_data = f.read()
result = process_pdf(pdf_data, OCRTool())

Processing BOLs: 100%|██████████| 15/15 [01:13<00:00,  4.87s/it]


In [ ]:
file_path = "AMAZON FREIGHT & CENTRAL FREIGHT (11 ORDERS) 05.30.24 (LIFEPRO)_page-0001.jpg"
image_data = base64.b64encode(open(file_path, "rb").read()).decode("utf-8")

ocr_tool = OCRTool()
result = ocr_tool.run(image_data)

In [16]:
PDF_PATH = "test_documents/chai6.11.pdf"
with open(PDF_PATH, "rb") as f:
    pdf_data = f.read()

bol_info_list = split_pdf(pdf_data)

ocr_tool = OCRTool()
for bol_info in tqdm(bol_info_list, desc="Processing BOLs"):
    img = bol_info["image"]
    pdf_bytes = bol_info["pdf"]
    shipment_info = ocr_tool.run(img)
    if shipment_info is None:
        continue
    order_number = shipment_info.get("customer_order_information", {}).get("order_number", "")
    shipment_id = shipment_info.get("customer_order_information", {}).get("shipment_id", "")
    file_name = f"Order {order_number} - Shipment {shipment_id}.pdf"
    bol_info["shipment_info"] = shipment_info
    bol_info["file_name"] = file_name

Processing BOLs: 100%|██████████| 15/15 [01:09<00:00,  4.61s/it]
